In [24]:
from IPython import get_ipython
get_ipython().magic('reset -sf')


In [25]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.base import BaseEstimator, ClassifierMixin
from scipy.optimize import minimize, LinearConstraint, NonlinearConstraint
from scipy import stats
import pickle

In [26]:
## 划分测试集和训练集
train_ratio = 0.8 # 训练集比例

data = pd.read_csv('seeds_dataset.txt', header=None, delim_whitespace=True) # delim_whitespace=True表示分割符为空白字符
data.info

labels = data.iloc[:, -1]
classes = labels.unique()
trainData = pd.DataFrame(data=None, index=None)
testData = pd.DataFrame(data=None, index=None)

for i in classes:
    classData = data.loc[labels==i, :]
    numTrain = round(train_ratio*classData.shape[0]) # 训练集样本数
    indices = np.random.permutation(classData.shape[0])
    
    trainData = pd.concat([trainData, classData.iloc[indices[0:numTrain], :]])
    testData = pd.concat([testData, classData.iloc[indices[numTrain:], :]])

trainData.info
testData.info                                            
trainData.to_csv('trainData.csv', header=0, index=0, sep='\t')
testData.to_csv('testData.csv', header=0, index=0, sep='\t')


In [27]:
## 获取训练和训练数据及归一化
X_train = trainData.iloc[:, :-1]
Y_train = trainData.iloc[:, -1].values
X_test = testData.iloc[:, :-1]
Y_test = testData.iloc[:, -1].values

# 使用StandardScaler类归一化
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)


In [28]:
## 定义超圆盘分类器类
class NHCmodel(BaseEstimator, ClassifierMixin):
    def __init__(self, ) -> None:
        super().__init__()
        self.sigma = 0.25
        self.classes = 0
        self.s_r = {}
        self.classifiers = {}
        self.predictData = None
        self.accuracy = 0

    def gaussian_kernel(self, x, y):
        return np.exp(-np.linalg.norm(x-y, ord=2, axis=1)**2 / (2 * (self.sigma ** 2)))
    
    def Objective_Function1(self, beta, X):
        """返回超圆盘的对偶问题的目标函数，在某一拉格朗日系数下的值
        Args:
            beta (ndarray): 为该输入样本集合下的拉格朗日系数
            X (ndarray): X为输入样本矩阵, 行为样本个数, 列为样本特征
        """
        beta = beta.reshape(-1, 1)
        print(X)
        return np.sum(beta*np.sum(X*X, 1).reshape(-1, 1))-np.sum((beta*X)@((beta*X).T))
    
    def Objective_Function2(self, alpha, X_plus, X_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        result = 0
        for i in range(M_plus):
            result = result + np.sum(alpha_plus[i]*alpha_plus*self.gaussian_kernel(X_plus[i, :], X_plus))
            - 2*np.sum(alpha_plus[i]*alpha_minus*self.gaussian_kernel(X_plus[i, :], X_minus))
        for i in range(M_minus):
            result = result + np.sum(alpha_minus[i]*alpha_minus*self.gaussian_kernel(X_minus[i, :], X_minus))
        return result
    
    def nonlcon(self, alpha, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        
        c = np.zeros((2, 1))
        for i in range(M_plus):
            c[0] = c[0] + np.sum(alpha_plus[i]*alpha_plus*self.gaussian_kernel(X_plus[i, :],X_plus))
            - np.sum(alpha_plus[i]*beta_plus*self.gaussian_kernel(X_plus[i, :], X_plus))
            + np.sum(beta_plus[i]*beta_plus*self.gaussian_kernel(X_plus[i, :], X_plus))
        c[0] -= r_plus**2
        for i in range(M_minus):
            c[0] = c[0] + np.sum(alpha_minus[i]*alpha_minus*self.gaussian_kernel(X_minus[i, :],X_minus))
            - np.sum(alpha_minus[i]*beta_minus*self.gaussian_kernel(X_minus[i, :], X_minus))
            + np.sum(beta_minus[i]*beta_minus*self.gaussian_kernel(X_minus[i, :], X_minus))
        c[1] -= r_minus**2
        return c.flatten()

    def fit(self, X, y):
        # 拟合函数
        classes = np.unique(y)
        Num = np.size(classes)
        beta = np.zeros((Num, np.size(y)))
        s_and_r = np.ones((Num, np.shape(X)[1]+1))
        # 分类求解超圆盘对偶问题拉格朗日系数，以求解s和r
        for i in classes:
            Xx = X[y==i, :]
            M = np.shape(Xx)[0]
            # 设定拉格朗日系数beta初值,一个样本一个beta
            beta_init = np.ones((M, 1)) / M # 一维数组，但是在优化函数里面需要reshape乘二维数组才能运算
            # 设线性等式约束
            Aeq1 = np.ones((1, M))
            beq1 = np.array([1])
            linearConstraint1 = LinearConstraint(Aeq1, beq1, beq1)
            # 设定beta下界
            bounds = [(1e-6, None) for _ in range(M)] 
            # 求解beta
            result1 = minimize(self.Objective_Function1, beta_init, 
                            args=(Xx,), method='SLSQP', bounds=bounds, constraints=linearConstraint1,
                            )
            beta[i-1, :M] = result1.x
            
            s = np.sum(result1.x.reshape(-1, 1)*Xx, 0)
            r = np.max(np.linalg.norm(Xx-s, ord=2,axis=1))
            s_and_r[i-1, :] = np.concatenate([s, [r]])
            
            self.s_r = {'s': s,
                        'r': r}
        # 求解多个分类器的参数，即分类超平面参数，OVO策略
        Num_classifier = int(Num*(Num-1)/2)
        b_classifier = np.zeros((Num_classifier, 1))
        iter = 0
        for i in range(Num-1):
            for j in range(i+1, Num):
                iter += 1
                # 获取基本信息
                X_plus = X[y==i+1, :]
                X_minus = X[y==j+1, :]
                M_plus = np.shape(X_plus)[0]
                M_minus = np.shape(X_minus)[0]
                # 设定超平面参数初值，都为列
                alpha_plus = np.ones((M_plus, 1)) / M_plus
                alpha_minus = np.ones((M_minus, 1)) / M_minus
                alpha_init = np.concatenate((alpha_plus, alpha_minus), axis=0)
                # 设定线性等式约束
                Aeq2 = np.zeros((2, M_plus+M_minus))
                Aeq2[0,:M_plus] = 1;
                Aeq2[1, M_plus:] = 1
                beq2 = np.array([1, 1])
                linearConstraint2 = LinearConstraint(Aeq2, beq2, beq2)
                # 设定不等式约束
                r_plus = s_and_r[i, -1]
                r_minus = s_and_r[j, -1]
                beta_plus = beta[i, :M_plus]
                beta_minus = beta[j, :M_minus]
                lb = -np.inf
                ub = np.array([0, 0])
                # NonlinearConstraint(lambda x: NHCmodel.nonlcon(x, beta_plus, beta_minus, X_plus, X_minus, r_plus_minus), lb, ub)
                # 这个和@(beta)Objective_Function1(beta, X),@(beta) 表示输入要优化的值为beta，X不动，异曲同工
                nonlinearConstraint =  NonlinearConstraint(lambda x: NHCmodel.nonlcon(self, x, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus), lb, ub)
                constraints = [linearConstraint2, nonlinearConstraint]
                # 求解alpha
                result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
                                   method='SLSQP', constraints=constraints)
                alpha = result2.x
                alpha_plus = alpha[:M_plus]
                alpha_minus = alpha[M_plus:]
                # 求解b
                for k in range(M_plus):
                    b_classifier[iter-1] += np.sum(alpha_plus[k]*alpha_plus*self.gaussian_kernel(X_plus[k, :], X_plus))
                for k in range(M_minus):
                    b_classifier[iter-1] -= np.sum(alpha_minus[k]*alpha_minus*self.gaussian_kernel(X_minus[k, :], X_minus))
                b_classifier[iter-1] = -1/2*b_classifier[iter-1]
                b = b_classifier[iter-1]
                self.classes = Num
                self.classifiers[(i+1, j+1)] = {'X+': X_plus,
                                                'X-': X_minus,
                                                'alpha+': alpha_plus,
                                                'alpha-': alpha_minus,
                                                'b': b}    
        # 保存分类器参数字典
        with open('classifiers.pkl', 'wb') as f:
            pickle.dump(self.classifiers, f)
                                                
        return 0  
                

    def predict(self,X, y):
        fx = np.zeros((np.shape(X)[0], self.classes))
        indexclasses = 0
        fxij = np.zeros((np.shape(X)[0], self.classes))
        for (i, j), classifier in self.classifiers.items():
            indexclasses += 1
            X_pl = classifier['X+']
            X_mi = classifier['X-']
            alpha_pl = classifier['alpha+']
            alpha_mi = classifier['alpha-']
            bb = classifier['b']
            
            M_plus = np.shape(X_pl)[0]
            M_minus = np.shape(X_mi)[0]
            
            for g in range(M_plus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] + alpha_pl[g]*self.gaussian_kernel(X_pl[g, :], X).reshape(-1)
            for g in range(M_minus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] - alpha_mi[g]*self.gaussian_kernel(X_mi[g, :], X).reshape(-1)
            
            fx[:, indexclasses-1] = np.sign(fx[:, indexclasses-1] + bb)
            fxij[:, indexclasses-1] = fx[:, indexclasses-1] 
            fx[:, indexclasses-1][fx[:, indexclasses-1]==1] = i
            fx[:, indexclasses-1][fx[:, indexclasses-1]==-1] = j
            fx[:, indexclasses-1][fx[:, indexclasses-1]==0] = 0


        y_pred = np.apply_along_axis(lambda x: np.argmax(np.bincount(x.astype(int))), axis=1, arr=fx) # axis表示假如你是n×m维度，axis=0，表示在n方向上，axis=1，表示在m方向上
        accuray = np.sum(y_pred==y) / np.size(y)
        y = y.reshape(-1, 1)
        y_pred = y_pred.reshape(-1, 1)
        self.predictData = np.concatenate((X, y, y_pred, fxij, fx), axis=1)
        self.accuracy = accuray
        print('accuray = ', accuray)
        return y_pred
              

In [29]:
## 训练
model = NHCmodel()
model.fit(X_train_scaled, Y_train)

C:\Users\lenovo\AppData\Local\Temp\ipykernel_5844\1468052902.py:76: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(self.Objective_Function1, beta_init,


[[-1.85513003e-01 -1.52280469e-01  3.49707930e-02  1.99996944e-03
  -2.04313325e-01 -1.58774721e+00 -5.28080070e-01]
 [-5.73315767e-01 -5.59336997e-01 -1.65663423e-01 -5.24391987e-01
  -5.27520844e-01  3.12352040e-01 -6.55232385e-01]
 [-6.43246399e-02 -6.01167267e-02  3.53368570e-01 -1.48077737e-01
  -1.84690011e-02 -6.91376489e-02 -3.86571848e-01]
 [-1.75125429e-01 -1.36919845e-01  3.49707930e-02 -1.34637943e-01
  -3.03968977e-01 -1.48686290e+00 -2.20453500e-01]
 [-2.47838447e-01 -1.29239533e-01 -5.84378308e-01  6.47190111e-02
  -3.68610480e-01 -4.12545179e-01 -4.74758131e-01]
 [-1.19657021e+00 -1.31200756e+00 -1.52578583e-01 -1.39125874e+00
  -1.12006796e+00 -6.61081369e-01 -1.64168825e+00]
 [ 4.64761496e-02  1.47251693e-01 -2.65980531e-01  3.58154527e-01
  -5.61765450e-02 -1.26839157e+00 -8.33655795e-01]
 [ 1.53134276e-02 -1.06198598e-01  1.25622254e+00 -5.49031611e-01
   3.93620586e-01 -1.70199369e+00 -6.55232385e-01]
 [-2.65151071e-01 -3.59648889e-01  8.41869270e-01 -4.68392843e-0

C:\Users\lenovo\AppData\Local\Temp\ipykernel_5844\1468052902.py:76: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(self.Objective_Function1, beta_init,


[[ 1.75350081e+00  1.80619905e+00  1.48372741e-01  2.34276420e+00
   1.33900258e+00 -2.92285733e-01  2.34310124e+00]
 [ 2.07897813e+00  1.90604311e+00  1.36526288e+00  1.83877190e+00
   2.06352610e+00  8.86256842e-01  1.87345801e+00]
 [ 1.34492290e+00  1.25321660e+00  1.16026705e+00  1.21606142e+00
   1.42788465e+00 -3.80475994e-01  1.32383188e+00]
 [ 1.34146038e+00  1.23785598e+00  1.22569125e+00  1.07942351e+00
   1.62450256e+00  3.33063389e-01  1.19873040e+00]
 [ 1.62538740e+00  1.66795344e+00  2.66136303e-01  1.69093416e+00
   1.36324314e+00 -1.48151804e+00  1.77501751e+00]
 [ 1.28605998e+00  1.13801192e+00  1.51791934e+00  9.13666039e-01
   1.60026199e+00  1.54434326e+00  9.62883369e-01]
 [ 1.58729963e+00  1.48362595e+00  1.16462866e+00  1.08390344e+00
   1.68645066e+00  4.13236353e-01  1.23359475e+00]
 [ 5.31229604e-01  5.23586974e-01  6.45596667e-01  1.99116958e-01
   6.97974334e-01  3.52438522e-01  4.31714826e-01]
 [ 1.33107280e+00  1.36074097e+00  4.01346318e-01  1.32133981e+0

C:\Users\lenovo\AppData\Local\Temp\ipykernel_5844\1468052902.py:76: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(self.Objective_Function1, beta_init,


[[-0.83646764 -0.88959041 -0.05226147 -0.88054655 -0.67027083  0.86688171
  -0.5342326 ]
 [-1.24850808 -1.22752413 -1.30404452 -1.21206148 -1.35439341  0.41390446
  -0.83570664]
 [-0.7187418  -0.84350854  0.61942699 -1.05078394 -0.37669067  0.79071739
  -1.0120792 ]
 [-1.24850808 -1.31200756 -0.67597219 -1.20534158 -1.24396418  0.19743746
  -0.83365579]
 [-0.99228125 -0.80510698 -2.04551879 -0.50199233 -1.31937927  2.20643832
  -0.28197881]
 [-1.40432169 -1.33504849 -2.0149875  -1.00598463 -1.71261508  0.77735523
  -0.65318154]
 [-0.98881873 -0.9510329  -0.93766899 -0.62519045 -1.2278038   0.38851636
  -0.20404675]
 [-1.08230689 -0.80510698 -2.77390823 -0.41463366 -1.58333207  0.46000392
  -0.19994506]
 [-0.95765601 -0.99711477 -0.34448957 -0.88054655 -0.78339346  0.29564934
  -0.81109651]
 [-0.58024082 -0.69758261  0.71974409 -0.88054655 -0.09119069  3.09034525
  -0.72085939]
 [-1.36623392 -1.35808943 -1.4305313  -1.30614004 -1.47828963  1.14147411
  -0.74341867]
 [-1.20349526 -1.1430

C:\Users\lenovo\AppData\Local\Temp\ipykernel_5844\1468052902.py:121: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
C:\Users\lenovo\AppData\Local\Temp\ipykernel_5844\1468052902.py:121: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
C:\Users\lenovo\AppData\Local\Temp\ipykernel_5844\1468052902.py:121: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),


0

In [30]:
# 测试
model.predict(X_test_scaled, Y_test)

accuray =  0.9285714285714286


array([[1],
       [1],
       [1],
       [3],
       [1],
       [1],
       [1],
       [1],
       [1],
       [1],
       [1],
       [2],
       [1],
       [1],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [2],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [3],
       [2],
       [3]], dtype=int64)

In [31]:
predictdata = model.predictData